In [1]:
import pandas as pd
import numpy as np
import regex as re
import json

## Preparation of document format from sentence format

In [2]:
# Import json
with open("Macocu-mt-en.json", "r") as file:
	tus_content = json.load(file)

In [3]:
# Convert data to a dataframe

corpus_df = pd.DataFrame(tus_content)

corpus_df.head()

score_bicleaner_ai biroamer_entities translation_direction  \
0               0.999                No               en-orig   
1               1.000                No               mt-orig   
2               1.000                No               en-orig   
3               1.000                No               en-orig   
4               0.534                No               mt-orig   

                                           en_source en_par_id  \
0  https://eur-lex.europa.eu/legal-content/en/TXT...    p319s0   
1  https://www.europarl.europa.eu/doceo/document/...    p168s0   
2  https://eur-lex.europa.eu/legal-content/EN/ALL...   p1082s0   
3  https://www.europarl.europa.eu/doceo/document/...    p890s0   
4  https://www.etwinning.net/en/pub/support/esafe...    p44s10   

                                              en_par en_var_doc en_var_dom  \
0  18 Income support is a means-tested benefit fo...          A          B   
1  Stresses the importance of taking into account...          B          B   
2  In addition, the Commission shall inform the E...          B          B   
3  Emphasises the importance of correlation table...          B          B   
4   Where should mobile phones be kept during class?          B          B   

                                           mt_source mt_par_id  \
0  https://eur-lex.europa.eu/legal-content/MT/TXT...    p285s0   
1  https://www.europarl.europa.eu/doceo/document/...    p168s0   
2  https://eur-lex.europa.eu/legal-content/MT/ALL...   p1082s0   
3  https://www.europarl.europa.eu/doceo/document/...    p890s0   
4  https://www.etwinning.net/mt/pub/support/esafe...     p44s9   

                                              mt_par  
0  L-appoġġ tad-dħul huwa benefiċċju mogħti skont...  
1  Jenfasizza l-importanza li jiġu meqjusa l-konk...  
2  B'żieda ma' dan, il-Kummissjoni għandha tavża ...  
3  Jenfasizza l-importanza tat-tabelli ta' korrel...  
4    Fejn għandhom jinżammu l-mobajls waqt l-iskola?

In [4]:
# Analyze distribution
corpus_df.describe(include="all")

score_bicleaner_ai biroamer_entities translation_direction  \
count         1.231654e+06           1231654               1231654   
unique                 NaN                 2                     2   
top                    NaN                No               en-orig   
freq                   NaN           1119473                748325   
mean          9.270704e-01               NaN                   NaN   
std           1.457151e-01               NaN                   NaN   
min           5.000000e-01               NaN                   NaN   
25%           9.870000e-01               NaN                   NaN   
50%           1.000000e+00               NaN                   NaN   
75%           1.000000e+00               NaN                   NaN   
max           1.000000e+00               NaN                   NaN   

                                                en_source en_par_id  \
count                                             1231654   1231654   
unique                                              47206     60140   
top     https://eur-lex.europa.eu/legal-content/EN/TXT...     p71s0   
freq                                                 4307      4548   
mean                                                  NaN       NaN   
std                                                   NaN       NaN   
min                                                   NaN       NaN   
25%                                                   NaN       NaN   
50%                                                   NaN       NaN   
75%                                                   NaN       NaN   
max                                                   NaN       NaN   

                                                   en_par en_var_doc  \
count                                             1231654    1231654   
unique                                            1079173          4   
top     It shall take effect the day following the pub...          B   
freq                                                  156    1010364   
mean                                                  NaN        NaN   
std                                                   NaN        NaN   
min                                                   NaN        NaN   
25%                                                   NaN        NaN   
50%                                                   NaN        NaN   
75%                                                   NaN        NaN   
max                                                   NaN        NaN   

       en_var_dom                                          mt_source  \
count     1231654                                            1231654   
unique          4                                              39512   
top             B  https://eur-lex.europa.eu/legal-content/MT/ALL...   
freq      1115740                                               6943   
mean          NaN                                                NaN   
std           NaN                                                NaN   
min           NaN                                                NaN   
25%           NaN                                                NaN   
50%           NaN                                                NaN   
75%           NaN                                                NaN   
max           NaN                                                NaN   

       mt_par_id                                             mt_par  
count    1231654                                            1231654  
unique     58327                                            1055075  
top        p72s0  Dan ir-Regolament għandu jidħol fis-seħħ fl-għ...  
freq        4599                                                 59  
mean         NaN                                                NaN  
std          NaN                                                NaN  
min          NaN                                                NaN  
25%          NaN        

In [5]:
# Sort by english url and then by en_par_id to order the paragraphs into texts
corpus_df = corpus_df.sort_values(by = ["en_source", "en_par_id"])

corpus_df

score_bicleaner_ai biroamer_entities translation_direction  \
909321               0.748                No               en-orig   
395349               1.000               Yes               en-orig   
526680               1.000               Yes               mt-orig   
126009               1.000               Yes               en-orig   
474818               1.000                No               mt-orig   
...                    ...               ...                   ...   
124325               1.000                No               en-orig   
295619               1.000                No               mt-orig   
175171               0.994                No               en-orig   
592233               0.993                No               en-orig   
505767               0.999                No               mt-orig   

                                                en_source    en_par_id  \
909321  http://akkuza.blogspot.com/2005/09/bushism-fak...         p5s1   
395349  http://akkuza.blogspot.com/2005/10/no-to-racis...  p22s0+p23s0   
526680  http://akkuza.blogspot.com/2005/10/no-to-racis...        p23s1   
126009  http://akkuza.blogspot.com/2005/10/no-to-racis...  p24s0+p24s1   
474818  http://akkuza.blogspot.com/2005/10/no-to-racis...  p24s2+p24s3   
...                                                   ...          ...   
124325  https://zebbugprimaryschool.wordpress.com/2021...        p36s1   
295619  https://zebbugprimaryschool.wordpress.com/2021...        p36s3   
175171  https://zminijietna.blogspot.com/2015/10/press...         p5s0   
592233  https://zminijietna.blogspot.com/2015/10/press...         p7s0   
505767  https://zminijietna.blogspot.com/2015/10/press...    p7s1+p8s0   

                                                   en_par en_var_doc  \
909321  He concludes by saying: "Yesterday, 3 Brazilia...        UNK   
395349  APPEAL TO BOYCOTT THE GENERAL WORKERS UNION On...          B   
526680  During the Congress meeting held on the same d...          B   
126009  Among other things Mr. Sammut is reported to h...          B   
474818  We feel that this type of language is not wort...          B   
...                                                   ...        ...   
124325  The programme consists of 8 sessions of 1.5 ho...        UNK   
295619  These themes will be discussed through fun and...        UNK   
175171  Żminijietna - Voice of the Left appealed to th...        UNK   
592233  "We therefore urge the Government to increase ...        UNK   
505767  These include an increase in the minimum wage;...        UNK   

       en_var_dom                                          mt_source  \
909321          B     https://mt.eferrit.com/cajt-politiku-klassiku/   
395349          B  https://markvella.wordpress.com/2005/10/07/app...   
526680          B  https://markvella.wordpress.com/2005/10/07/app...   
126009          B  https://markvella.wordpress.com/2005/10/07/app...   
474818          B  https://markvella.wordpress.com/2005/10/07/app...   
...           ...                                                ...   
124325          B  https://siggiewiprimary.wordpress.com/2021/05/...   
295619          B  https://siggiewiprimary.wordpress.com/2021/05/...   
175171          B    http://www.zminijietna.org/prs/2013/180713.html   
592233          B    http://www.zminijietna.org/prs/2013/180713.html   
505767          B    http://www.zminijietna.org/prs/2013/180713.html   

        mt_par_id                                             mt_par  
909321      p80s1  Huwa jikkonkludi billi qal: "Il-bieraħ, 3 suld...  
395349       p5s0  Nhar l-Erbgħa l-5 ta' Ottubru, il-membri tal-G...  
526680       p5s1  Dakinhar, fid-diskors tiegħu lill-Kungress, is...  
126009       p6s0  Fost affarijiet oħra, is-Sur Sammut ġie rrapur...  
474818       p6s1  Inħossu li dan it-tip ta' kliem mhuwiex xieraq...  
...           ...                                                ...  
124325      p25s4  Dan il-programm jikkonsisti fi 8

In [6]:
corpus_df.en_source.sample(n=10).to_list()[:5]

['https://www.europarl.europa.eu/doceo/document/A-8-2019-0064_EN.html',
 'https://eur-lex.europa.eu/legal-content/EN/ALL/?uri=CELEX:31992L0012',
 'https://newsbook.com.mt/en/catamaran-to-ferry-pope-to-gozo/',
 'https://eur-lex.europa.eu/legal-content/EN/TXT/HTML/?uri=OJ:L:2013:180:FULL&amp;from=PT',
 'https://eur-lex.europa.eu/legal-content/EN/TXT/?uri=CELEX%3A52020PC0405']

In [7]:
# Add information about domains
domain_re=re.compile(r'^https?://(?:www\.)?(.+?)[/$]')
#domain_re = re.compile('(?:https|http)?:\/\/(?:www\.)?(?:en|is|english|m|old|prod|staging)?(?:\.)?(.*?)\.(?:com|net|is|org|edu|info|biz|fun|cat|space|club|museum|gov|site|digital|int|store|coop|dev|online|blog|kpmg|mobi|guru|help|bible|art|academy|top|one|live)\/')

# Check whether the expression catches everything
for i in corpus_df.en_source.to_list():
	try:
		result =  domain_re.search(i).group(1)

	except AttributeError:
		print(i)

# Check whether the expression catches everything
for i in corpus_df.mt_source.to_list():
	try:
		result =  domain_re.search(i).group(1)

	except AttributeError:
		print(i)

In [8]:
en_domain_list = [domain_re.search(i).group(1) for i in corpus_df.en_source.to_list()]

en_domain_list[:3]

['akkuza.blogspot.com', 'akkuza.blogspot.com', 'akkuza.blogspot.com']

In [9]:
corpus_df["en_domain"] = en_domain_list

corpus_df.head(2)

score_bicleaner_ai biroamer_entities translation_direction  \
909321               0.748                No               en-orig   
395349               1.000               Yes               en-orig   

                                                en_source    en_par_id  \
909321  http://akkuza.blogspot.com/2005/09/bushism-fak...         p5s1   
395349  http://akkuza.blogspot.com/2005/10/no-to-racis...  p22s0+p23s0   

                                                   en_par en_var_doc  \
909321  He concludes by saying: "Yesterday, 3 Brazilia...        UNK   
395349  APPEAL TO BOYCOTT THE GENERAL WORKERS UNION On...          B   

       en_var_dom                                          mt_source  \
909321          B     https://mt.eferrit.com/cajt-politiku-klassiku/   
395349          B  https://markvella.wordpress.com/2005/10/07/app...   

       mt_par_id                                             mt_par  \
909321     p80s1  Huwa jikkonkludi billi qal: "Il-bieraħ, 3 suld...   
395349      p5s0  Nhar l-Erbgħa l-5 ta' Ottubru, il-membri tal-G...   

                  en_domain  
909321  akkuza.blogspot.com  
395349  akkuza.blogspot.com

In [10]:
# Repeat with Maltese domain
sl_domain_list = [domain_re.search(i).group(1) for i in corpus_df.mt_source.to_list()]
corpus_df["mt_domain"] = sl_domain_list

corpus_df.head(2)

score_bicleaner_ai biroamer_entities translation_direction  \
909321               0.748                No               en-orig   
395349               1.000               Yes               en-orig   

                                                en_source    en_par_id  \
909321  http://akkuza.blogspot.com/2005/09/bushism-fak...         p5s1   
395349  http://akkuza.blogspot.com/2005/10/no-to-racis...  p22s0+p23s0   

                                                   en_par en_var_doc  \
909321  He concludes by saying: "Yesterday, 3 Brazilia...        UNK   
395349  APPEAL TO BOYCOTT THE GENERAL WORKERS UNION On...          B   

       en_var_dom                                          mt_source  \
909321          B     https://mt.eferrit.com/cajt-politiku-klassiku/   
395349          B  https://markvella.wordpress.com/2005/10/07/app...   

       mt_par_id                                             mt_par  \
909321     p80s1  Huwa jikkonkludi billi qal: "Il-bieraħ, 3 suld...   
395349      p5s0  Nhar l-Erbgħa l-5 ta' Ottubru, il-membri tal-G...   

                  en_domain                mt_domain  
909321  akkuza.blogspot.com           mt.eferrit.com  
395349  akkuza.blogspot.com  markvella.wordpress.com

In [11]:
# Add information whether the domains are the same
corpus_df["same_domains"] = np.where(corpus_df["en_domain"] == corpus_df["mt_domain"], "yes", 'no')

# Add column for domains that are different
corpus_df["different_domains"] = corpus_df["en_domain"] + " " + corpus_df["mt_domain"]

corpus_df.head(2)

score_bicleaner_ai biroamer_entities translation_direction  \
909321               0.748                No               en-orig   
395349               1.000               Yes               en-orig   

                                                en_source    en_par_id  \
909321  http://akkuza.blogspot.com/2005/09/bushism-fak...         p5s1   
395349  http://akkuza.blogspot.com/2005/10/no-to-racis...  p22s0+p23s0   

                                                   en_par en_var_doc  \
909321  He concludes by saying: "Yesterday, 3 Brazilia...        UNK   
395349  APPEAL TO BOYCOTT THE GENERAL WORKERS UNION On...          B   

       en_var_dom                                          mt_source  \
909321          B     https://mt.eferrit.com/cajt-politiku-klassiku/   
395349          B  https://markvella.wordpress.com/2005/10/07/app...   

       mt_par_id                                             mt_par  \
909321     p80s1  Huwa jikkonkludi billi qal: "Il-bieraħ, 3 suld...   
395349      p5s0  Nhar l-Erbgħa l-5 ta' Ottubru, il-membri tal-G...   

                  en_domain                mt_domain same_domains  \
909321  akkuza.blogspot.com           mt.eferrit.com           no   
395349  akkuza.blogspot.com  markvella.wordpress.com           no   

                                  different_domains  
909321           akkuza.blogspot.com mt.eferrit.com  
395349  akkuza.blogspot.com markvella.wordpress.com

In [12]:
corpus_df["same_domains"].value_counts()

yes    1102557
no      129097
Name: same_domains, dtype: int64

In [13]:
# Analyze instances from different domains
print(corpus_df[corpus_df["same_domains"] != "yes"]["different_domains"] .value_counts().to_markdown())

|                                                                                |   different_domains |
|:-------------------------------------------------------------------------------|--------------------:|
| eur-lex.europa.eu europarl.europa.eu                                           |               51554 |
| jw.org wol.jw.org                                                              |               22318 |
| europarl.europa.eu eur-lex.europa.eu                                           |               18424 |
| wol.jw.org jw.org                                                              |                2687 |
| curia.europa.eu eur-lex.europa.eu                                              |                2405 |
| newsbook.com.mt netnews.com.mt                                                 |                2396 |
| church.mt laikosblog.org                                                       |                1021 |
| ec.europa.eu eur-lex.europa.eu                       

In [14]:
# Discard instances that are from different domains
corpus_df = corpus_df[corpus_df["same_domains"] == "yes"]
corpus_df.describe(include="all")

score_bicleaner_ai biroamer_entities translation_direction  \
count         1.102557e+06           1102557               1102557   
unique                 NaN                 2                     2   
top                    NaN                No               en-orig   
freq                   NaN           1009332                674229   
mean          9.285861e-01               NaN                   NaN   
std           1.448570e-01               NaN                   NaN   
min           5.000000e-01               NaN                   NaN   
25%           9.920000e-01               NaN                   NaN   
50%           1.000000e+00               NaN                   NaN   
75%           1.000000e+00               NaN                   NaN   
max           1.000000e+00               NaN                   NaN   

                                                en_source en_par_id  \
count                                             1102557   1102557   
unique                                              37949     56357   
top     https://eur-lex.europa.eu/legal-content/EN/TXT...     p71s0   
freq                                                 4301      4150   
mean                                                  NaN       NaN   
std                                                   NaN       NaN   
min                                                   NaN       NaN   
25%                                                   NaN       NaN   
50%                                                   NaN       NaN   
75%                                                   NaN       NaN   
max                                                   NaN       NaN   

                                                   en_par en_var_doc  \
count                                             1102557    1102557   
unique                                             993175          4   
top     It shall take effect the day following the pub...          B   
freq                                                  111     921398   
mean                                                  NaN        NaN   
std                                                   NaN        NaN   
min                                                   NaN        NaN   
25%                                                   NaN        NaN   
50%                                                   NaN        NaN   
75%                                                   NaN        NaN   
max                                                   NaN        NaN   

       en_var_dom                                          mt_source  \
count     1102557                                            1102557   
unique          4                                              33044   
top             B  https://eur-lex.europa.eu/legal-content/MT/ALL...   
freq      1017157                                               6943   
mean          NaN                                                NaN   
std           NaN                                                NaN   
min           NaN                                                NaN   
25%           NaN                                                NaN   
50%           NaN                                                NaN   
75%           NaN                                                NaN   
max           NaN                                                NaN   

       mt_par_id                                             mt_par  \
count    1102557                                            1102557   
unique     54499                                             975828   
top        p72s0  Dan ir-Regolament għandu jidħol fis-seħħ fl-għ...   
freq        4321                                                 47   
mean         NaN                                                NaN   
std          NaN                                                NaN   
min          NaN                                                NaN   
25%          NaN

In [15]:
# Calculate average bicleaner ai score based on the en_source
corpus_df["average_score"] = corpus_df["score_bicleaner_ai"].groupby(corpus_df['en_source']).transform('mean')

corpus_df.head(2)

/tmp/ipykernel_18710/1031930680.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  corpus_df["average_score"] = corpus_df["score_bicleaner_ai"].groupby(corpus_df['en_source']).transform('mean')


score_bicleaner_ai biroamer_entities translation_direction  \
1069829               0.526               Yes               mt-orig   
1129134               0.555                No               en-orig   

                                           en_source en_par_id  \
1069829                  http://alsmalta.org/donate/    p102s0   
1129134  http://amberalert.com.mt/amber-alert-malta/     p13s1   

                                                    en_par en_var_doc  \
1069829  This I wish that you help me to make as much d...          B   
1129134  AMBER Alert Europe connects law enforcement wi...          B   

        en_var_dom                                          mt_source  \
1069829        MIX             https://alsmalta.org/stories-patients/   
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   

        mt_par_id                                             mt_par  \
1069829     p84s1  Ma tliftx żmien iżda pruvajt nagħmel minn koll...   
1129134     p13s1  L-AMBER Alert Europe iqarreb lill-forzi tal-or...   

                 en_domain          mt_domain same_domains  \
1069829       alsmalta.org       alsmalta.org          yes   
1129134  amberalert.com.mt  amberalert.com.mt          yes   

                           different_domains  average_score  
1069829            alsmalta.org alsmalta.org         0.5260  
1129134  amberalert.com.mt amberalert.com.mt         0.8833

In [16]:
# Join par id and text
corpus_df["en-par-text"] = corpus_df["en_par_id"] + "-" + corpus_df["en_par"]
corpus_df.head(2)

/tmp/ipykernel_18710/3160425621.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  corpus_df["en-par-text"] = corpus_df["en_par_id"] + "-" + corpus_df["en_par"]


score_bicleaner_ai biroamer_entities translation_direction  \
1069829               0.526               Yes               mt-orig   
1129134               0.555                No               en-orig   

                                           en_source en_par_id  \
1069829                  http://alsmalta.org/donate/    p102s0   
1129134  http://amberalert.com.mt/amber-alert-malta/     p13s1   

                                                    en_par en_var_doc  \
1069829  This I wish that you help me to make as much d...          B   
1129134  AMBER Alert Europe connects law enforcement wi...          B   

        en_var_dom                                          mt_source  \
1069829        MIX             https://alsmalta.org/stories-patients/   
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   

        mt_par_id                                             mt_par  \
1069829     p84s1  Ma tliftx żmien iżda pruvajt nagħmel minn koll...   
1129134     p13s1  L-AMBER Alert Europe iqarreb lill-forzi tal-or...   

                 en_domain          mt_domain same_domains  \
1069829       alsmalta.org       alsmalta.org          yes   
1129134  amberalert.com.mt  amberalert.com.mt          yes   

                           different_domains  average_score  \
1069829            alsmalta.org alsmalta.org         0.5260   
1129134  amberalert.com.mt amberalert.com.mt         0.8833   

                                               en-par-text  
1069829  p102s0-This I wish that you help me to make as...  
1129134  p13s1-AMBER Alert Europe connects law enforcem...

In [17]:
# Find duplicated English sentences that have the same par id
corpus_df[corpus_df["en-par-text"].duplicated(keep=False)]

score_bicleaner_ai biroamer_entities translation_direction  \
71895                1.000                No               mt-orig   
570618               1.000                No               en-orig   
120664               0.998                No               en-orig   
454759               1.000                No               en-orig   
32699                1.000                No               en-orig   
...                    ...               ...                   ...   
296678               1.000                No               en-orig   
429269               0.726               Yes               mt-orig   
636082               0.997               Yes               mt-orig   
635499               0.550                No               en-orig   
423055               0.521                No               en-orig   

                                                en_source en_par_id  \
71895   http://epso.europa.eu/job-opportunities/instit...     p43s0   
570618  http://epso.europa.eu/job-opportunities/instit...     p43s0   
120664  http://epso.europa.eu/job-opportunities/instit...     p43s0   
454759  http://epso.europa.eu/job-opportunities/instit...     p43s0   
32699   http://epso.europa.eu/job-opportunities/instit...     p42s2   
...                                                   ...       ...   
296678  https://www.um.edu.mt/about/strategy/strategic...      p3s0   
429269  https://www.um.edu.mt/library/oar/handle/12345...     p20s0   
636082  https://www.um.edu.mt/library/oar/handle/12345...     p20s0   
635499                              https://youth.gov.mt/      p3s1   
423055                      https://youth.gov.mt/page/54/      p3s1   

                                                   en_par en_var_doc  \
71895   Who can apply: Nationals of a Member State of ...          B   
570618  Who can apply: Nationals of a Member State of ...          B   
120664  Who can apply: University graduates who are ei...        UNK   
454759  Who can apply: University graduates who are ei...        UNK   
32699   Every year Europol offers a number of internsh...        UNK   
...                                                   ...        ...   
296678  The University of Malta embarked on a Strategi...        UNK   
429269  Mallia Borg writes an article in dedication to...        UNK   
636082  Mallia Borg writes an article in dedication to...        UNK   
635499  Through Eurodesk, the European Youth Charter a...          B   
423055  Through Eurodesk, the European Youth Charter a...          B   

       en_var_dom                                          mt_source  \
71895           B  https://epso.europa.eu/job-opportunities/insti...   
570618          B  https://epso.europa.eu/job-opportunities/insti...   
120664          B  https://epso.europa.eu/job-opportunities/insti...   
454759          B  https://epso.europa.eu/job-opportunities/insti...   
32699           B  https://epso.europa.eu/job-opportunities/insti...   
...           ...                                                ...   
296678          B  https://www.um.edu.mt/about/pjanstrategiku/pro...   
429269          B  https://www.um.edu.mt/library/oar/handle/12345...   
636082          B  https://www.um.edu.mt/library/oar/handle/12345...   
635499          B                    https://youth.gov.mt/mt/page/3/   
423055          B                https://youth.gov.mt/mt/our-agency/   

          mt_par_id                                             mt_par  \
71895         p42s0  Min jista' japplika: It-trainees jintgħażlu mi...   
570618        p43s0  Min jista' japplika: Ċittadini ta' Stat Membru...   
120664  p44s0+p45s0  Min jista' japplika: Gradwati tal-università l...   
454759        p43s0  Min jista' japplika: Gradwati universitarji li...   
32699         p42s2  Kull sena l-Europol toffri numru ta' internshi...   
...             ...                                                ...   
296678         p3s0  L-Università ta' Malta nehdiet proċess tal-Ip

In [18]:
# Discard all duplicated English paragraphs with the same par id
corpus_df = corpus_df.drop_duplicates("en-par-text")

In [22]:
# Number of discarded texts
37949 - 37666

283

In [23]:
# Number of discarded sentences
1102557 - 1038369

64188

In [19]:
corpus_df.describe(include="all")

score_bicleaner_ai biroamer_entities translation_direction  \
count         1.038369e+06           1038369               1038369   
unique                 NaN                 2                     2   
top                    NaN                No               en-orig   
freq                   NaN            949734                631755   
mean          9.270893e-01               NaN                   NaN   
std           1.462272e-01               NaN                   NaN   
min           5.000000e-01               NaN                   NaN   
25%           9.910000e-01               NaN                   NaN   
50%           1.000000e+00               NaN                   NaN   
75%           1.000000e+00               NaN                   NaN   
max           1.000000e+00               NaN                   NaN   

                                                en_source en_par_id  \
count                                             1038369   1038369   
unique                                              37666     56357   
top     https://eur-lex.europa.eu/legal-content/EN/TXT...     p71s0   
freq                                                 4259      3858   
mean                                                  NaN       NaN   
std                                                   NaN       NaN   
min                                                   NaN       NaN   
25%                                                   NaN       NaN   
50%                                                   NaN       NaN   
75%                                                   NaN       NaN   
max                                                   NaN       NaN   

                                                   en_par en_var_doc  \
count                                             1038369    1038369   
unique                                             993175          4   
top     It shall take effect the day following the pub...          B   
freq                                                   93     863958   
mean                                                  NaN        NaN   
std                                                   NaN        NaN   
min                                                   NaN        NaN   
25%                                                   NaN        NaN   
50%                                                   NaN        NaN   
75%                                                   NaN        NaN   
max                                                   NaN        NaN   

       en_var_dom                                          mt_source  \
count     1038369                                            1038369   
unique          4                                              32548   
top             B  https://eur-lex.europa.eu/legal-content/MT/ALL...   
freq       953683                                               6873   
mean          NaN                                                NaN   
std           NaN                                                NaN   
min           NaN                                                NaN   
25%           NaN                                                NaN   
50%           NaN                                                NaN   
75%           NaN                                                NaN   
max           NaN                                                NaN   

       mt_par_id                                             mt_par  \
count    1038369                                            1038369   
unique     53874                                             948857   
top        p72s0  Dan ir-Regolament għandu jidħol fis-seħħ fl-għ...   
freq        4017                                                 32   
mean         NaN                                                NaN   
std          NaN                                                NaN   
min          NaN                                                NaN   
25%          NaN

In [20]:
# Add to each instance from the same en_source joint text from all sentences
corpus_df["en_doc"] = corpus_df["en_par"].groupby(corpus_df['en_source']).transform(' '.join)

corpus_df.head(2)

score_bicleaner_ai biroamer_entities translation_direction  \
1069829               0.526               Yes               mt-orig   
1129134               0.555                No               en-orig   

                                           en_source en_par_id  \
1069829                  http://alsmalta.org/donate/    p102s0   
1129134  http://amberalert.com.mt/amber-alert-malta/     p13s1   

                                                    en_par en_var_doc  \
1069829  This I wish that you help me to make as much d...          B   
1129134  AMBER Alert Europe connects law enforcement wi...          B   

        en_var_dom                                          mt_source  \
1069829        MIX             https://alsmalta.org/stories-patients/   
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   

        mt_par_id                                             mt_par  \
1069829     p84s1  Ma tliftx żmien iżda pruvajt nagħmel minn koll...   
1129134     p13s1  L-AMBER Alert Europe iqarreb lill-forzi tal-or...   

                 en_domain          mt_domain same_domains  \
1069829       alsmalta.org       alsmalta.org          yes   
1129134  amberalert.com.mt  amberalert.com.mt          yes   

                           different_domains  average_score  \
1069829            alsmalta.org alsmalta.org         0.5260   
1129134  amberalert.com.mt amberalert.com.mt         0.8833   

                                               en-par-text  \
1069829  p102s0-This I wish that you help me to make as...   
1129134  p13s1-AMBER Alert Europe connects law enforcem...   

                                                    en_doc  
1069829  This I wish that you help me to make as much d...  
1129134  AMBER Alert Europe connects law enforcement wi...

In [21]:
# Repeat with the text in other language
corpus_df["mt_doc"] = corpus_df["mt_par"].groupby(corpus_df['mt_source']).transform(' '.join)
corpus_df.head(2)

score_bicleaner_ai biroamer_entities translation_direction  \
1069829               0.526               Yes               mt-orig   
1129134               0.555                No               en-orig   

                                           en_source en_par_id  \
1069829                  http://alsmalta.org/donate/    p102s0   
1129134  http://amberalert.com.mt/amber-alert-malta/     p13s1   

                                                    en_par en_var_doc  \
1069829  This I wish that you help me to make as much d...          B   
1129134  AMBER Alert Europe connects law enforcement wi...          B   

        en_var_dom                                          mt_source  \
1069829        MIX             https://alsmalta.org/stories-patients/   
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   

        mt_par_id                                             mt_par  \
1069829     p84s1  Ma tliftx żmien iżda pruvajt nagħmel minn koll...   
1129134     p13s1  L-AMBER Alert Europe iqarreb lill-forzi tal-or...   

                 en_domain          mt_domain same_domains  \
1069829       alsmalta.org       alsmalta.org          yes   
1129134  amberalert.com.mt  amberalert.com.mt          yes   

                           different_domains  average_score  \
1069829            alsmalta.org alsmalta.org         0.5260   
1129134  amberalert.com.mt amberalert.com.mt         0.8833   

                                               en-par-text  \
1069829  p102s0-This I wish that you help me to make as...   
1129134  p13s1-AMBER Alert Europe connects law enforcem...   

                                                    en_doc  \
1069829  This I wish that you help me to make as much d...   
1129134  AMBER Alert Europe connects law enforcement wi...   

                                                    mt_doc  
1069829  Ma tliftx żmien iżda pruvajt nagħmel minn koll...  
1129134  L-AMBER Alert Europe iqarreb lill-forzi tal-or...

In [22]:
# Keep only one example of each text
corpus_df = corpus_df.drop_duplicates("en_doc")

corpus_df.shape

(37581, 19)

In [23]:
corpus_df.describe(include="all")

score_bicleaner_ai biroamer_entities translation_direction  \
count         37581.000000             37581                 37581   
unique                 NaN                 2                     2   
top                    NaN                No               en-orig   
freq                   NaN             29806                 22157   
mean              0.908431               NaN                   NaN   
std               0.152586               NaN                   NaN   
min               0.500000               NaN                   NaN   
25%               0.859000               NaN                   NaN   
50%               0.999000               NaN                   NaN   
75%               1.000000               NaN                   NaN   
max               1.000000               NaN                   NaN   

                          en_source en_par_id  \
count                         37581     37581   
unique                        37581      3928   
top     http://alsmalta.org/donate/    p100s0   
freq                              1      1715   
mean                            NaN       NaN   
std                             NaN       NaN   
min                             NaN       NaN   
25%                             NaN       NaN   
50%                             NaN       NaN   
75%                             NaN       NaN   
max                             NaN       NaN   

                                                   en_par en_var_doc  \
count                                               37581      37581   
unique                                              37274          4   
top     Having regard to the Treaty establishing the E...          B   
freq                                                    5      18870   
mean                                                  NaN        NaN   
std                                                   NaN        NaN   
min                                                   NaN        NaN   
25%                                                   NaN        NaN   
50%                                                   NaN        NaN   
75%                                                   NaN        NaN   
max                                                   NaN        NaN   

       en_var_dom                                          mt_source  \
count       37581                                              37581   
unique          4                                              29604   
top             B  https://eur-lex.europa.eu/legal-content/MT/ALL...   
freq        32488                                                  9   
mean          NaN                                                NaN   
std           NaN                                                NaN   
min           NaN                                                NaN   
25%           NaN                                                NaN   
50%           NaN                                                NaN   
75%           NaN                                                NaN   
max           NaN                                                NaN   

       mt_par_id                                             mt_par  \
count      37581                                              37581   
unique      3666                                              35111   
top       p100s0  - Forms - Deċiżjoni Qafas tal-Kunsill 2009/829...   
freq        1150                                                 10   
mean         NaN                                                NaN   
std          NaN                                                NaN   
min          NaN                                                NaN   
25%          NaN                                                NaN   
50%          NaN                                                NaN   
75%          NaN                                                NaN   
max          NaN                                                NaN

In [24]:
# Add information about length
corpus_df["en_length"] = corpus_df.en_doc.str.split().str.len()

corpus_df.head(3)

score_bicleaner_ai biroamer_entities translation_direction  \
1069829               0.526               Yes               mt-orig   
1129134               0.555                No               en-orig   
840121                1.000                No               en-orig   

                                                 en_source en_par_id  \
1069829                        http://alsmalta.org/donate/    p102s0   
1129134        http://amberalert.com.mt/amber-alert-malta/     p13s1   
840121   http://catholicvoices.mt/a-number-of-reactions...     p13s0   

                                                    en_par en_var_doc  \
1069829  This I wish that you help me to make as much d...          B   
1129134  AMBER Alert Europe connects law enforcement wi...          B   
840121   A number of reactions to the Manifesto “Rebuil...          B   

        en_var_dom                                          mt_source  \
1069829        MIX             https://alsmalta.org/stories-patients/   
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   
840121           B  http://catholicvoices.mt/numru-ta-reazzjonijie...   

        mt_par_id                                             mt_par  \
1069829     p84s1  Ma tliftx żmien iżda pruvajt nagħmel minn koll...   
1129134     p13s1  L-AMBER Alert Europe iqarreb lill-forzi tal-or...   
840121      p14s0  Ir-reazzjonijiet li waslu minn numru ta' kandi...   

                 en_domain          mt_domain same_domains  \
1069829       alsmalta.org       alsmalta.org          yes   
1129134  amberalert.com.mt  amberalert.com.mt          yes   
840121   catholicvoices.mt  catholicvoices.mt          yes   

                           different_domains  average_score  \
1069829            alsmalta.org alsmalta.org       0.526000   
1129134  amberalert.com.mt amberalert.com.mt       0.883300   
840121   catholicvoices.mt catholicvoices.mt       0.902923   

                                               en-par-text  \
1069829  p102s0-This I wish that you help me to make as...   
1129134  p13s1-AMBER Alert Europe connects law enforcem...   
840121   p13s0-A number of reactions to the Manifesto “...   

                                                    en_doc  \
1069829  This I wish that you help me to make as much d...   
1129134  AMBER Alert Europe connects law enforcement wi...   
840121   A number of reactions to the Manifesto “Rebuil...   

                                                    mt_doc  en_length  
1069829  Ma tliftx żmien iżda pruvajt nagħmel minn koll...         23  
1129134  L-AMBER Alert Europe iqarreb lill-forzi tal-or...        223  
840121   Ir-reazzjonijiet li waslu minn numru ta' kandi...        288

In [25]:
print(corpus_df.en_length.describe().to_markdown())

|       |   en_length |
|:------|------------:|
| count |   37581     |
| mean  |     838.355 |
| std   |    3183.44  |
| min   |       2     |
| 25%   |      48     |
| 50%   |     142     |
| 75%   |     440     |
| max   |  123935     |


In [26]:
# Add information about Maltese length
corpus_df["mt_length"] = corpus_df.mt_doc.str.split().str.len()

corpus_df.head(3)

score_bicleaner_ai biroamer_entities translation_direction  \
1069829               0.526               Yes               mt-orig   
1129134               0.555                No               en-orig   
840121                1.000                No               en-orig   

                                                 en_source en_par_id  \
1069829                        http://alsmalta.org/donate/    p102s0   
1129134        http://amberalert.com.mt/amber-alert-malta/     p13s1   
840121   http://catholicvoices.mt/a-number-of-reactions...     p13s0   

                                                    en_par en_var_doc  \
1069829  This I wish that you help me to make as much d...          B   
1129134  AMBER Alert Europe connects law enforcement wi...          B   
840121   A number of reactions to the Manifesto “Rebuil...          B   

        en_var_dom                                          mt_source  \
1069829        MIX             https://alsmalta.org/stories-patients/   
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   
840121           B  http://catholicvoices.mt/numru-ta-reazzjonijie...   

        mt_par_id  ...          en_domain          mt_domain same_domains  \
1069829     p84s1  ...       alsmalta.org       alsmalta.org          yes   
1129134     p13s1  ...  amberalert.com.mt  amberalert.com.mt          yes   
840121      p14s0  ...  catholicvoices.mt  catholicvoices.mt          yes   

                           different_domains average_score  \
1069829            alsmalta.org alsmalta.org      0.526000   
1129134  amberalert.com.mt amberalert.com.mt      0.883300   
840121   catholicvoices.mt catholicvoices.mt      0.902923   

                                               en-par-text  \
1069829  p102s0-This I wish that you help me to make as...   
1129134  p13s1-AMBER Alert Europe connects law enforcem...   
840121   p13s0-A number of reactions to the Manifesto “...   

                                                    en_doc  \
1069829  This I wish that you help me to make as much d...   
1129134  AMBER Alert Europe connects law enforcement wi...   
840121   A number of reactions to the Manifesto “Rebuil...   

                                                    mt_doc en_length  \
1069829  Ma tliftx żmien iżda pruvajt nagħmel minn koll...        23   
1129134  L-AMBER Alert Europe iqarreb lill-forzi tal-or...       223   
840121   Ir-reazzjonijiet li waslu minn numru ta' kandi...       288   

         mt_length  
1069829         49  
1129134        207  
840121         227  

[3 rows x 21 columns]

In [27]:
# Analyze Maltese length
corpus_df.mt_length.describe()

count     37581.000000
mean       1375.139964
std        4834.227989
min           2.000000
25%          65.000000
50%         187.000000
75%         697.000000
max      178307.000000
Name: mt_length, dtype: float64

In [28]:
# Discard instances that have length less than  79 (median from other datasets - if we would choose the median of this dataset, we would lose useful texts)
corpus_df = corpus_df[corpus_df["en_length"] > 78]

corpus_df.shape

(24104, 21)

In [29]:
corpus_df.columns

Index(['score_bicleaner_ai', 'biroamer_entities', 'translation_direction',
       'en_source', 'en_par_id', 'en_par', 'en_var_doc', 'en_var_dom',
       'mt_source', 'mt_par_id', 'mt_par', 'en_domain', 'mt_domain',
       'same_domains', 'different_domains', 'average_score', 'en-par-text',
       'en_doc', 'mt_doc', 'en_length', 'mt_length'],
      dtype='object')

In [30]:
# Discard irrelevant columns
corpus_df = corpus_df.drop(columns = ['score_bicleaner_ai', 'en_par_id', 'en_par', 'mt_par_id', 'mt_par', 'en-par-text', 'same_domains', 'different_domains'])

In [31]:
corpus_df.head(1)

biroamer_entities translation_direction  \
1129134                No               en-orig   

                                           en_source en_var_doc en_var_dom  \
1129134  http://amberalert.com.mt/amber-alert-malta/          B          B   

                                                 mt_source          en_domain  \
1129134  http://www.amberalert.com.mt/mt/amber-alert-ma...  amberalert.com.mt   

                 mt_domain  average_score  \
1129134  amberalert.com.mt         0.8833   

                                                    en_doc  \
1129134  AMBER Alert Europe connects law enforcement wi...   

                                                    mt_doc  en_length  \
1129134  L-AMBER Alert Europe iqarreb lill-forzi tal-or...        223   

         mt_length  
1129134        207

In [32]:
# Filter out the non-textual texts

# Calculate ratio of punctuations per words

def paragraph_punct_ratio(text):
    token_re=re.compile(r'\w+|\S',re.UNICODE)
    tokens=token_re.findall(text)
    punct=len([e for e in tokens if e in '.;,!?:'])
    ratio = punct/len(tokens)
    return ratio

corpus_df["punct_ratio"] = corpus_df.en_doc.apply(paragraph_punct_ratio)

corpus_df.head(3)

biroamer_entities translation_direction  \
1129134                No               en-orig   
840121                 No               en-orig   
4581                  Yes               en-orig   

                                                 en_source en_var_doc  \
1129134        http://amberalert.com.mt/amber-alert-malta/          B   
840121   http://catholicvoices.mt/a-number-of-reactions...          B   
4581     http://catholicvoices.mt/pope-francis-says-pan...          B   

        en_var_dom                                          mt_source  \
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   
840121           B  http://catholicvoices.mt/numru-ta-reazzjonijie...   
4581             B  http://catholicvoices.mt/papa-frangisku-jghid-...   

                 en_domain          mt_domain  average_score  \
1129134  amberalert.com.mt  amberalert.com.mt       0.883300   
840121   catholicvoices.mt  catholicvoices.mt       0.902923   
4581     catholicvoices.mt  catholicvoices.mt       0.876624   

                                                    en_doc  \
1129134  AMBER Alert Europe connects law enforcement wi...   
840121   A number of reactions to the Manifesto “Rebuil...   
4581     In an exclusive interview recorded for The Tab...   

                                                    mt_doc  en_length  \
1129134  L-AMBER Alert Europe iqarreb lill-forzi tal-or...        223   
840121   Ir-reazzjonijiet li waslu minn numru ta' kandi...        288   
4581     F'intervista esklussiva għal TheTablet — l-eww...       2243   

         mt_length  punct_ratio  
1129134        207     0.083665  
840121         227     0.094801  
4581          1834     0.103216

In [33]:
corpus_df.punct_ratio.describe()

count    24104.000000
mean         0.077243
std          0.023548
min          0.000000
25%          0.062874
50%          0.073577
75%          0.088484
max          0.389279
Name: punct_ratio, dtype: float64

In [36]:
# With the ratio < 0.015 we catch non-textual texts without any punctuation
for i in corpus_df.query("punct_ratio < 0.015").en_doc.to_list()[:5]:
	print(i)

European Parliament legislative resolution on the application by the Czech Republic to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Cyprus to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Latvia to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Lithuania to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Hungary to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Malta to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Poland to become a member of the European Union European Parliament legislative resolution on the application by the Republic of Slovenia to becom

In [37]:
# With ratio above 0.2, we catch non-textual texts with a lot of punctuations
for i in corpus_df.query("punct_ratio > 0.2").en_doc.to_list():
	print(i)

Reflect: You and I are one of those vines. The fruits of the Holy Spirit, according to St. Paul, are: happiness; patience; righteousness; faithfulness; and control. Jesus expects these fruits from me and you. If Jesus, the son of the owner of the vineyard, had to come now seeking these fruits, what will he find? Pray: Forgive me God and, in your mercy, forget my guilt. “Come again, God Almighty; look down from heaven, and visit this vineyard. Do your utmost to live according to God’s Spirit, and let His will be done!
0:03:47.719,0:03:52.499 For by how much the more pains ye take to[br]please the world, by so much the more shall 0:03:52.499,0:03:57.169 ye for ever go thankless! 0:03:59.043,0:04:04.699 But gulp down your tears and hie aloft to[br]the royal-mast with your hearts; for your 0:04:04.699,0:04:09.046 friends who have gone before are clearing[br]out the seven-storied heavens, and making 0:04:09.046,0:04:15.619 refugees of long-pampered Gabriel, Michael,[br]and Raphael, against 

The analysis showed that filtering of non-textual texts is necessary.

In [38]:
# Filter the corpus by using only instances with ratio between 0.015 and 0.2
corpus_df = corpus_df.query("punct_ratio >= 0.015 & punct_ratio <= 0.2")

corpus_df.head()

biroamer_entities translation_direction  \
1129134                No               en-orig   
840121                 No               en-orig   
4581                  Yes               en-orig   
730369                 No               en-orig   
1057522                No               mt-orig   

                                                 en_source en_var_doc  \
1129134        http://amberalert.com.mt/amber-alert-malta/          B   
840121   http://catholicvoices.mt/a-number-of-reactions...          B   
4581     http://catholicvoices.mt/pope-francis-says-pan...          B   
730369   http://catholicvoices.mt/rebuilding-community-...          B   
1057522  http://catholicvoices.mt/update-2-further-reac...          B   

        en_var_dom                                          mt_source  \
1129134          B  http://www.amberalert.com.mt/mt/amber-alert-ma...   
840121           B  http://catholicvoices.mt/numru-ta-reazzjonijie...   
4581             B  http://catholicvoices.mt/papa-frangisku-jghid-...   
730369           B  http://catholicvoices.mt/nibnu-mill-gdid-il-ko...   
1057522          B  http://catholicvoices.mt/aggornament-2-aktar-r...   

                 en_domain          mt_domain  average_score  \
1129134  amberalert.com.mt  amberalert.com.mt       0.883300   
840121   catholicvoices.mt  catholicvoices.mt       0.902923   
4581     catholicvoices.mt  catholicvoices.mt       0.876624   
730369   catholicvoices.mt  catholicvoices.mt       0.839125   
1057522  catholicvoices.mt  catholicvoices.mt       0.832100   

                                                    en_doc  \
1129134  AMBER Alert Europe connects law enforcement wi...   
840121   A number of reactions to the Manifesto “Rebuil...   
4581     In an exclusive interview recorded for The Tab...   
730369   Inspired by the declaration of European Bishop...   
1057522  Update 2 – Further reactions to the Manifesto ...   

                                                    mt_doc  en_length  \
1129134  L-AMBER Alert Europe iqarreb lill-forzi tal-or...        223   
840121   Ir-reazzjonijiet li waslu minn numru ta' kandi...        288   
4581     F'intervista esklussiva għal TheTablet — l-eww...       2243   
730369   Ispirati mid-dikjarazzjoni tal-Isqfijiet Ewrop...        888   
1057522  Aġġornament 2 – Aktar reazzjonijiet għall-mani...        268   

         mt_length  punct_ratio  
1129134        207     0.083665  
840121         227     0.094801  
4581          1834     0.103216  
730369         779     0.071503  
1057522        206     0.058824

In [40]:
24104 - 23999

105

In [39]:
corpus_df.shape

(23999, 14)

In [41]:
# Save the dataframe to csv
corpus_df.to_csv("Macocu-mt-en-doc-format-filtered.csv", sep= "\t")

## Analysis of prepared corpus

In [42]:
# Inspect corpus information
corpus_df.describe(include="all")

biroamer_entities translation_direction  \
count              23999                 23999   
unique                 2                     2   
top                   No               en-orig   
freq               19579                 14181   
mean                 NaN                   NaN   
std                  NaN                   NaN   
min                  NaN                   NaN   
25%                  NaN                   NaN   
50%                  NaN                   NaN   
75%                  NaN                   NaN   
max                  NaN                   NaN   

                                          en_source en_var_doc en_var_dom  \
count                                         23999      23999      23999   
unique                                        23999          4          4   
top     http://amberalert.com.mt/amber-alert-malta/          B          B   
freq                                              1      15212      21149   
mean                                            NaN        NaN        NaN   
std                                             NaN        NaN        NaN   
min                                             NaN        NaN        NaN   
25%                                             NaN        NaN        NaN   
50%                                             NaN        NaN        NaN   
75%                                             NaN        NaN        NaN   
max                                             NaN        NaN        NaN   

                                                mt_source           en_domain  \
count                                               23999               23999   
unique                                              20183                 310   
top     https://eur-lex.europa.eu/legal-content/MT/ALL...  europarl.europa.eu   
freq                                                    8                5589   
mean                                                  NaN                 NaN   
std                                                   NaN                 NaN   
min                                                   NaN                 NaN   
25%                                                   NaN                 NaN   
50%                                                   NaN                 NaN   
75%                                                   NaN                 NaN   
max                                                   NaN                 NaN   

                 mt_domain  average_score  \
count                23999   23999.000000   
unique                 310            NaN   
top     europarl.europa.eu            NaN   
freq                  5589            NaN   
mean                   NaN       0.917170   
std                    NaN       0.063733   
min                    NaN       0.500000   
25%                    NaN       0.883162   
50%                    NaN       0.929562   
75%                    NaN       0.962129   
max                    NaN       1.000000   

                                                   en_doc  \
count                                               23999   
unique                                              23999   
top     AMBER Alert Europe connects law enforcement wi...   
freq                                                    1   
mean                                                  NaN   
std                                                   NaN   
min                                                   NaN   
25%                                                   NaN   
50%                                                   NaN   
75%                                                   NaN   
max                                                   NaN   

                                                   mt_doc      en_length  \
count                                               23999   23999.000000   
unique                                              20181            NaN   
top   

In [43]:
# Inspect en_var_doc statistics
print(corpus_df.en_var_doc.value_counts(normalize = True).to_markdown())

|     |   en_var_doc |
|:----|-------------:|
| B   |    0.63386   |
| UNK |    0.241593  |
| A   |    0.0928372 |
| MIX |    0.0317097 |


In [44]:
print(corpus_df.en_var_dom.value_counts(normalize = True).to_markdown())

|     |   en_var_dom |
|:----|-------------:|
| B   |  0.881245    |
| A   |  0.113005    |
| MIX |  0.00504188  |
| UNK |  0.000708363 |


In [45]:
# Inspect translation direction
print(corpus_df.translation_direction.value_counts(normalize = True).to_markdown())

|         |   translation_direction |
|:--------|------------------------:|
| en-orig |                  0.5909 |
| mt-orig |                  0.4091 |


In [46]:
print(corpus_df.average_score.describe().to_markdown())

|       |   average_score |
|:------|----------------:|
| count |   23999         |
| mean  |       0.91717   |
| std   |       0.0637326 |
| min   |       0.5       |
| 25%   |       0.883162  |
| 50%   |       0.929562  |
| 75%   |       0.962129  |
| max   |       1         |


In [47]:
print(corpus_df.en_length.describe().to_markdown())

|       |   en_length |
|:------|------------:|
| count |    23999    |
| mean  |     1290.69 |
| std   |     3911.68 |
| min   |       79    |
| 25%   |      153    |
| 50%   |      300    |
| 75%   |      853    |
| max   |   123935    |


In [49]:
# Inspect duplicated Maltese texts
pd.set_option('display.max_colwidth', None)
duplicated = corpus_df[corpus_df.mt_doc.duplicated(keep=False)].sort_values("mt_doc")
duplicated[["mt_doc", "en_doc", "average_score"]]

mt_doc  \
1053162  "Artikolu 13 Ftuħ u għeluq ta' intervent pubbliku (a) għandu jkun miftuħ għal butir u trab ta' ħalib xkumat; Sabiex jitqiesu l-karatteristiċi speċifiċi fil-kummerċ bejn l-Unjoni u ċerti pajjiżi terzi, il-Kummissjoni għandu jkollha s-setgħa li tadotta atti delegati f'konformita mal-Artikolu 227 dwar derogi minn din it-Taqsima fir-rigward ta' prodotti li għandhom jiġu esportati fejn ikun meħtieġ bil-liġi tal-pajjiż terz ikkonċernat. L-Istati Membri li jagħmlu użu mill-alternattivi msemmija f'dan l-Artikolu għandhom jinnotifikaw lill-Kummissjoni dwar kif jiġu applikati. L-Istati Membri li jagħmlu użu mill-alternattivi msemmija f'dan l-Artikolu għandhom jinnotifikaw lill-Kummissjoni dwar kif jiġu applikati. (e) regoli dwar id-dħul ta' membri ġodda, u partikolarment il-perijodu minimu ta' sħubija, li ma jistax ikun anqas minn sena; (e) regoli dwar id-dħul ta' membri ġodda, u partikolarment il-perijodu minimu ta' sħubija, li ma jistax ikun anqas minn sena; Il-protezzjoni msemmija fil-paragrafu 1 ta' dan l-Artikolu għandha tapplika wkoll għal oġġetti fi tranżitu skont it-tifsira tal-punt 44 tal-Artikolu 3 tar-Regolament (UE) 2017/625 li jidħlu fit-territorju doganali tal-Unjoni mingħajr ma jkunu rilaxxati għaċ-ċirkolazzjoni libera fi ħdan it-territorju doganali tal-Unjoni u fir-rigward ta' oġġetti mibjugħa permezz ta' mezzi ta' komunikazzjoni mill-bogħod; Dawn l-awtoritajiet għandhom joffru garanziji adegwati ta' oġġettività u imparzjalità, u għandhom ikollhom għad-dispożizzjoni tagħhom il-persunal kwalifikat u r-riżorsi meħtieġa biex iwettqu l-funzjonijiet tagħhom." L-Istat Membru konċernat għandu jinforma lill-Kummissjoni dwar kwalunkwe ftehim li l-kamp ta' applikazzjoni tiegħu jiġi estiż skont dan l-Artikolu. (4) L-Anness II tar-Regolament (UE) Nru 1308/2013 jistabbilixxi ċerti definizzjonijiet dwar setturi li jaqgħu fil-kamp ta' applikazzjoni ta' dak ir-Regolament. (3i) L-Artikolu 16 huwa ssostitwit b'dan li ġej: Artikolu 16 (c) kwalunkwe indikazzjoni jew prattika kummerċjali oħra li x'aktarx tiżgwida lill-konsumaturi fir-rigward tan-natura vera jew il-kompożizzjoni tal-prodott. Madankollu, din id-dispożizzjoni ma għandhiex tapplika għad-denominazzjoni ta' prodotti li n-natura eżatta tagħhom tkun ċara mill-użu tradizzjonali tagħhom u/jew meta d-denominazzjonijiet jintużaw b'mod ċar sabiex jiddeskrivu kwalità li tkun karatteristika tal-prodott. Il-Kummissjoni tista' tadotta atti ta' implimentazzjoni li jistipulaw regoli dwar il-forma tal-ispeċifikazzjoni. Il-Kummissjoni tista' tadotta atti ta' implimentazzjoni li jistipulaw regoli dwar il-forma tal-ispeċifikazzjoni. (a) id-definizzjonijiet, id-denominazzjoni u d-deskrizzjonijiet ta' bejgħ tekniċi għas-setturi minbarra dawk stabbiliti fl-Artikolu 78; Il-Kummissjoni għandha tingħata s-setgħa li tadotta atti ddelegati f'konformità mal-Artikolu 227 dwar il-bidla, deroga jew eżenzjoni għad-definizzjonijiet u d-deskrizzjonijiet tal-bejgħ li dwarhom hemm dispożizzjoni fl-Anness VII. (a) "denominazzjoni ta' oriġini" tfisser l-isem ta' reġjun, post speċifiku jew, f'każijiet eċċezzjonali u debitament ġustifikabbli, pajjiż użat biex jiddeskrivi prodott imsemmi fl-Artikolu 92(1): Denominazzjoni protetta ta' oriġini u indikazzjoni ġeografika protetta jistgħu jintużaw minn kwalunkwe operatur li jikkummerċjalizza nbid li jkun ġie magħmul f'konformità mal-ispeċifikazzjoni korrispondenti ta' prodott. Denominazzjoni protetta ta' oriġini u indikazzjoni ġeografika protetta, kif ukoll l-inbid li juża dak l-isem protett f'konformità mal-ispeċifikazzjonijiet ta' prodotti għandhom ikunu protetti kontra: (i) minn prodotti komparabbli li mhumiex konformi ma' l-ispeċifikazzjoni tal-prodott tal-isem protett; jew (ii) sakemm dan l-użu jisfrutta, idgħajjef jew inaqqas ir-reputazzjoni ta' denominazzjoni ta' oriġini jew ta' indikazzjoni ġeografika, inkluż meta isem irreġistrat jintuża bħala ingredjent; (b) kwalunkwe użu ħażin, imitazzjoni jew evokazzjoni, anke jekk l-oriġini vera tal-prodott j